In [ ]:
%pip install pandas
%pip install numpy

In [ ]:
import json
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np

In [ ]:
def df_stats(df):
    print(df.info())
    # print(sessions.describe())
    print(df.head())


In [ ]:
sessions_path = 'content/sessions.jsonl'

sessions = pd.read_json(file_path, lines=True, encoding='utf-8')

df_stats(sessions)

tracks_path = 'content/tracks.jsonl'

tracks = pd.read_json(tracks_path, lines=True, encoding='utf-8')

df_stats(tracks)


users_path = 'content/users.jsonl'

users = pd.read_json(users_path, lines=True, encoding='utf-8')

df_stats(users)

artists_path = 'content/artists.jsonl'

artists = pd.read_json(artists_path, lines=True, encoding='utf-8')

df_stats(artists)




@TODO:
Definicja tych atrbutów:
- Ilość wysłuchanych piosenek
- Średnia ilość wysłuchanych piosenek w sesji
- Ilość sesji
- Skip rate na sesje
- Czas słuchania w serwisie
- Czas słuchania w miesiącu
- średni czas słuchania dzienny
- Czas słuchania w jednej sesji
- Ilość polubionych piosenek na wysłuchane


In [13]:
print(f'sessions: {sessions.columns}')
print(f'tracks: {tracks.columns}')
print(f'users: {users.columns}')
print(f'artists: {artists.columns}')


# result = df.loc[df['Attribute2'] == 'A', 'Attribute1'].values


sessions: Index(['timestamp', 'user_id', 'track_id', 'event_type', 'session_id'], dtype='object')
tracks: Index(['id', 'artist_id', 'name', 'popularity', 'duration_ms', 'explicit',
       'release_date', 'danceability', 'energy', 'key', 'mode', 'loudness',
       'speechiness', 'acousticness', 'instrumentalness', 'liveness',
       'valence', 'tempo', 'time_signature'],
      dtype='object')
users: Index(['user_id', 'name', 'city', 'street', 'favourite_genres',
       'premium_user'],
      dtype='object')
artists: Index(['id', 'name', 'genres'], dtype='object')


In [ ]:
track_id_duration = dict(zip(tracks['id'], tracks['duration_ms']))


{'6C0WWu7RYKbAgWUI3YC0sT': 249573, '4q7EBRq8ncztC2PRmEC7Fy': 254733, '7cNyONpVADZVrW9xe3qq4z': 279347, '1bKRTzTFz7wHMxpgZSuPR1': 193707, '56OEjuyZ3AROnv4aR1XqhD': 182120, '1F3s1BbWYoCBa8I84GhzZB': 156307, '7A6iCvA36tfeXuMHXa0hLD': 267200, '7wfJKiiCg7WivTsy6smzOD': 229827, '2gOmko3OtEwl1rWcJnaouJ': 209600, '3YhlQnsfgQhQHjt0nB5sEV': 344333, '6Mjarhbtmvf3oFQnnCW02I': 179773, '794LRMm5vapB2wM0pKzPuT': 269360, '2y1ig9EfhcTBjtApCQ59za': 191467, '3QjYT0uPHFoqmm1vUDly4X': 289440, '2NYafkxRb5MYEXOFDsKXT7': 350773, '3fuI1d6P8zqojJwMmr6PGb': 203053, '4ru4VcAOmoA8aYdEKVIa73': 424653, '6uPWtYdJnr6522sDLgLzY4': 243947, '5hs3HdOVAFjpvXkNkPppn4': 254093, '4T2mvqNOm67uvkCyfIHzPV': 233840, '1Pg6vg7X0jNpaC9wiMKvZw': 278827, '0nO5442fyqNDRglyfCMJJO': 291853, '4NebH0wqHPjJALLeGHpX7Z': 158976, '5YFBWNRDSxj4eO0rhp1MXg': 187947, '6FoEwwvNDdXMaShVDd3uEU': 231853, '2C5l2dK6ep2JRgQ9UenCBs': 196747, '6gP6uFJSsV1XsArB0tiAM8': 372160, '2sDsy2ctgFZh6djcCoOB8q': 258907, '45QGx07YVvExMryNW5T6nE': 255573, '2ziKr5ARPlaE

In [ ]:
sessions["event_type"].value_counts()

event_type
Play             845371
Skip             249903
Advertisement    191533
Like             165114
BuyPremium         1248
Name: count, dtype: int64

In [ ]:
# sessions: Index(['timestamp', 'user_id', 'track_id', 'event_type', 'session_id'], dtype='object')
# Map values to a new column using a dictionary
sessions['track_len'] = sessions['track_id'].map(track_id_duration)


sessions['duration_ms'] = 0
# [conditions, what to modify] = new value for selected by condtions columns to modify
sessions.loc[sessions['event_type'] == "Play", 'duration_ms'] = sessions['track_len']
sessions.loc[sessions['event_type'] == "Skip", 'duration_ms'] = -sessions['track_len']

sessions.head()
duration_played_ms = sessions.groupby("user_id")['duration_ms'].sum().reset_index()

users = pd.merge(users, duration_played_ms, on='user_id', how='left', suffixes=('', '_total'))
users.rename(columns={'duration_ms': 'total_time_songs_played_ms'}, inplace=True)

In [ ]:
sessions['song_played_in_full'] = sessions['event_type'].map({"Play":1,"Skip":-1,"Advertisement":0,"Like":0, "BuyPremium":0})

tracks_played_per_user = sessions.groupby(["user_id",'track_id', "session_id"])['song_played_in_full'].sum().reset_index()
mean_tracks_per_user_id = 
tracks_played_per_user.describe()

user_id     session_id  song_played_in_full
count  871736.000000  871736.000000        871736.000000
mean     1591.837591   20483.950526             0.683083
std       870.444682   11775.210019             0.465388
min       101.000000     124.000000             0.000000
25%       831.000000   10258.000000             0.000000
50%      1592.000000   20454.000000             1.000000
75%      2348.000000   30705.000000             1.000000
max      3100.000000   40816.000000             2.000000

In [62]:
users_extended.head()

user_id                 name       city        street  \
0      101      Jerzy Tatarczyk    Wyszków  Błękitna 928   
1      102        Rozalia Kujda      Konin     Polna 670   
2      103  Kazimierz Posłuszna      Żagań   Tęczowa 883   
3      104          Witold Cyba  Legionowo  Jesionowa 50   
4      105     Gustaw Bąkiewicz   Pruszków  Jeziorna 255   

                            favourite_genres  premium_user  \
0                     [lounge, rock, motown]         False   
1  [mellow gold, permanent wave, latin rock]         False   
2                [pop, ranchera, blues rock]         False   
3     [new romantic, new wave, country rock]         False   
4             [metal, rock en espanol, soul]         False   

   total_time_songs_played  
0                 31590809  
1                 16904227  
2                 39829642  
3                 73897470  
4                 10514275

In [ ]:
# @TODO muszę połączyć dane z tracks i z sessions żeby określić ile user słucha czego
# @ założe że przy skipie nie wysłuchał do końca i wywalam wtedy 1 z odpaleń

# # sessions["id"] = range(0,len(sessions))
# # sessions['song_id__session_id'] = sessions['track_id'].apply(lambda x: str(x)) + sessions['session_id'].apply(lambda x: str(x))

# sessions['full_play'] = sessions['event_type'].apply(lambda x: 1 if x == "Like" or x == "Play" else 0)
# sessions['Like'] = sessions['event_type'].apply(lambda x: 1 if x == "Like" else 0)
# sessions['Play'] = sessions['event_type'].apply(lambda x: 1 if x == "Play" else 0)
# sessions['Skip'] = sessions['event_type'].apply(lambda x: 1 if x == "Skip" else 0)



# df_stats(sessions)

In [ ]:
sessions = sessions.sort_values(by=['session_id', 'timestamp'])



In [ ]:
result = sessions.groupby(['track_id', 'session_id']).count()

# Display the result
print(result)

In [ ]:
print(sessions.groupby("song_id__session_id").apply())

In [ ]:


nr_songs_played = sessions.groupby('user_id').agg(
        {
                'id':'size',
                'event_type':[lambda x: 1 if skip]
        }
        ).reset_index()

print(nr_songs_played)